In [1]:
import os
import dask
import random
import torch
from torch.utils.data import Dataset, DataLoader

from dask.distributed import Client
import dask.dataframe as dd
import pandas as pd

from dask_ml.preprocessing import MinMaxScaler
from dask_ml.model_selection import train_test_split
from dask_ml.linear_model import LinearRegression

from daskdataset import DaskDataset, ShallowNet
import torch.nn as nn
import torch.nn.functional as F

In [9]:
client = Client()

sample_dataset="/home/hpcrsaxe/Desktop/Code/Dataset/sample_train_data/dataset1.parquet"

df = dd.read_parquet(sample_dataset, engine="fastparquet")#.repartition(npartitions=10)  #using pyarrow throws error with numpy

#### Run this only on the cluster

In [ ]:
client = Client(str(os.getenv('HOSTNAME')) + "-ib:8786")

sample_datasets=["/lustre/nec/ws3/ws/hpcrsaxe-hpcrsaxe/datasets/dataset1.parquet",
                 "/lustre/nec/ws3/ws/hpcrsaxe-hpcrsaxe/datasets/dataset2.parquet",
                 "/lustre/nec/ws3/ws/hpcrsaxe-hpcrsaxe/datasets/dataset3.parquet",
                 "/lustre/nec/ws3/ws/hpcrsaxe-hpcrsaxe/datasets/dataset4.parquet",
                 "/lustre/nec/ws3/ws/hpcrsaxe-hpcrsaxe/datasets/dataset5.parquet",
                 "/lustre/nec/ws3/ws/hpcrsaxe-hpcrsaxe/datasets/dataset6.parquet",
                 "/lustre/nec/ws3/ws/hpcrsaxe-hpcrsaxe/datasets/dataset7.parquet",
                 "/lustre/nec/ws3/ws/hpcrsaxe-hpcrsaxe/datasets/dataset8.parquet",]

df = dd.read_parquet(sample_datasets, engine="fastparquet") 

#### Convert old Parquet to new Parquet

In [8]:
# Compute the Dask dataframe to get a Pandas dataframe
df_pandas = df.compute()

# Create a new Pandas dataframe with the expanded 'features' columns
features_df = pd.DataFrame(df_pandas['features'].to_list(), columns=[f'feature_{i}' for i in range(len(df_pandas['features'][0]))])
labels_df = pd.DataFrame(df_pandas['labels'].to_list(), columns=[f'label_{i}' for i in range(len(df_pandas['labels'][0]))])

# Concatenate the original dataframe with the expanded features and labels dataframes
df_pandas = pd.concat([features_df, labels_df], axis=1)

#save df_pandas a parquet
df_pandas.to_parquet("/home/hpcrsaxe/Desktop/Code/Dataset/sample_train_data/dataset1.parquet", engine="fastparquet")

2023-11-28 16:43:12,666 - distributed.worker.memory - WARNING - Unmanaged memory use is high. This may indicate a memory leak or the memory may not be released to the OS; see https://distributed.dask.org/en/latest/worker-memory.html#memory-not-released-back-to-the-os for more information. -- Unmanaged memory: 2.72 GiB -- Worker memory limit: 3.86 GiB
2023-11-28 16:43:14,316 - distributed.worker.memory - WARNING - Worker is at 81% memory usage. Pausing worker.  Process memory: 3.13 GiB -- Worker memory limit: 3.86 GiB
2023-11-28 16:43:15,668 - distributed.nanny.memory - WARNING - Worker tcp://127.0.0.1:33977 (pid=48276) exceeded 95% memory budget. Restarting...
2023-11-28 16:43:15,946 - distributed.nanny - WARNING - Restarting worker
2023-11-28 16:43:21,786 - distributed.worker.memory - WARNING - Unmanaged memory use is high. This may indicate a memory leak or the memory may not be released to the OS; see https://distributed.dask.org/en/latest/worker-memory.html#memory-not-released-back

KilledWorker: Attempted to run task ('read-parquet-dfab612cdfb5b1c27377f316ddefebac', 0) on 3 different workers, but all those workers died while running it. The last worker that attempt to run the task was tcp://127.0.0.1:43435. Inspecting worker logs is often a good next step to diagnose what went wrong. For more information see https://distributed.dask.org/en/stable/killed.html.

In [10]:
#separate the features and labels
df_labels = df.loc[:, df.columns.str.contains('label')]

# Create a StandardScaler object
scaler_features = MinMaxScaler()
df_features_scaled = scaler_features.fit_transform(df.loc[:, df.columns.str.contains('feature')])

#Split the data into training and test sets
X_train, X_test, y_train, y_test = train_test_split(df_features_scaled, df_labels, shuffle=True)

In [19]:
X = torch.tensor(X_train.compute().values)
y = torch.tensor(y_train.compute().values)

2023-11-28 16:58:28,387 - distributed.worker.memory - WARNING - Worker is at 81% memory usage. Pausing worker.  Process memory: 3.16 GiB -- Worker memory limit: 3.86 GiB
2023-11-28 16:58:29,636 - distributed.worker.memory - WARNING - Worker is at 58% memory usage. Resuming worker. Process memory: 2.26 GiB -- Worker memory limit: 3.86 GiB


In [14]:
from skorch import NeuralNetRegressor
import torch.optim as optim

niceties = {
    "callbacks": False,
    "warm_start": False,
    "train_split": None,
    "max_epochs": 5,
}

model = NeuralNetRegressor(
    module=ShallowNet,
    module__n_features=X.size(dim=1),
    criterion=nn.MSELoss,
    optimizer=optim.SGD,
    optimizer__lr=0.1,
    optimizer__momentum=0.9,
    batch_size=64,
    **niceties,
)

2023-11-28 16:52:11,130 - distributed.worker.memory - WARNING - Worker is at 81% memory usage. Pausing worker.  Process memory: 3.15 GiB -- Worker memory limit: 3.86 GiB
2023-11-28 16:52:12,561 - distributed.worker.memory - WARNING - Worker is at 58% memory usage. Resuming worker. Process memory: 2.25 GiB -- Worker memory limit: 3.86 GiB


4860


In [ ]:
model.device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
model = model.share_memory()

In [20]:
model.fit(X, y)

Re-initializing module because the following parameters were re-set: n_features.
Re-initializing criterion.
Re-initializing optimizer.
  epoch    train_loss     dur
-------  ------------  ------
      1        0.3994  4.5545


<class 'skorch.regressor.NeuralNetRegressor'>[initialized](
  module_=ShallowNet(
    (layer1): Linear(in_features=4860, out_features=8, bias=True)
  ),
)

In [21]:
test_X = torch.tensor(X_test.compute().values)
test_y = torch.tensor(y_test.compute().values)

2023-11-28 17:00:11,618 - distributed.worker.memory - WARNING - Worker is at 81% memory usage. Pausing worker.  Process memory: 3.13 GiB -- Worker memory limit: 3.86 GiB
2023-11-28 17:00:13,143 - distributed.worker.memory - WARNING - Worker is at 57% memory usage. Resuming worker. Process memory: 2.22 GiB -- Worker memory limit: 3.86 GiB


In [22]:
print(model.score(test_X, test_y))

-3.410176609207851


In [ ]:
# Define the loss function and optimizer
criterion = torch.nn.CrossEntropyLoss()
optimizer = torch.optim.SGD(model.parameters(), lr=0.01)
# Move the model to the GPU
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
model = model.to(device)
# Distribute the model across workers
model = model.share_memory()

In [ ]:
# Train the model
for epoch in range(10):
    for batch in dataloader:
        # Split the batch across workers
        batch = [b.to(device) for b in batch]
        futures = client.map(lambda data: model(data[0]), batch)
        # Compute the loss
        losses = client.map(criterion, futures, batch[1])
        loss = client.submit(torch.mean, client.gather(losses))
        # Compute the gradients and update the model parameters
        optimizer.zero_grad()
        gradients = client.map(lambda loss, future: torch.autograd.grad(loss, future)[0], loss, futures)
        gradients =client.submit(torch.mean, client.gather(gradients))

In [ ]:
client.map(lambda parameter, gradient: parameter.grad.copy_(gradient), model.parameters(), gradients)
optimizer.step()

In [ ]:
from dask_ml.linear_model import LinearRegression
from sklearn.linear_model import LinearRegression

# Initialize the Linear Regression model
model = LinearRegression()
model.fit(X_train, y_train)


In [ ]:
new_dask_df = df['features'].apply(pd.Series, meta=meta)
new_dask_df.compute()

In [ ]:
# Use this code for PyArrow tables

#import pyarrow as pa

# Define schema for features and labels columns
#schema = pa.schema({
    #'features': pa.list_(pa.float32()),
    #'labels': pa.list_(pa.float32())
#})

#import pyarrow.parquet as pq
#df = dd.from_pandas(pq.read_table(sample_dataset, schema=schema).to_pandas(), npartitions=10)